# MCMC - Tutorial

This notebook contains material covered in the lectures 'Introduction to MCMC'. The goal is to learn how to code your own Metropolis/Metropolis-Hastings MCMC sampler. If you get stuck, you can find the full solutions online at http://icg.port.ac.uk/~schewtsj/TPCosmoV/L3/IntroductionToMCMC-solutions.ipynb, but to derive maximum benefit from the exercise, you should try doing this yourself before checking the solutions. 

To run all cells in this notebook, you will need to have installed the following software packages:
1. emcee (http://dfm.io/emcee/current/)
2. corner.py (https://github.com/dfm/corner.py)
3. GetDist (https://getdist.readthedocs.io/en/latest/)
4. scipy
5. numpy
6. matplotlib

### Import packages and some default plot settings 

In [1]:
from __future__ import print_function

import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline
from matplotlib import rc
import time
import random as rd

import corner
import emcee
from getdist import plots, MCSamples
import getdist

rc('font',**{'family':'sans-serif'})
rc('text', usetex=True)
rc('axes', linewidth=1.3)
rc('font', **{'weight':'bold'})



ImportError: No module named corner

# Simple Metropolis MCMC sampler

### Exercise 1: Define general functions to calculate the log prior, log likelihood and log posterior. 

The form of these functions is general, but for use in any specific problem you will need to rewrite the likelihood and prior functions accordingly. In particular, for the first examples below I want to sample from specified posteriors, so for now the data vector is not really "data", but simply contains the required mean values of the parameters themselves.

In [ ]:
def lnprior(theta):
    """
    Return the log prior for given theta location
    Parameters:
    -----------
    theta:   numpy array
             vector location in parameter space
    """
    
    # TODO: implement flat log prior on each parameter from -10 to 10
    # Hint: log(0) = -np.inf
    ...
    
    return result
    
def lnlike(theta, data, covmat):
    """
    Return the log likelihood for given theta 
    Parameters:
    -----------
    theta:   numpy array, length D
             vector location in parameter space
    data:    numpy array, length N
             the data vector  
    covmat:  numpy array, dimensions NxN
             covariance matrix for data points
    """
    
    # default option: "data" vector actually specifies the mean parameter values (i.e. also N=D here)
    # TODO implement log Likelihood
    # Hint: like = exp(-Chi^2)
    ...
    
    return result

def lnprob(theta, data, covmat):
    """
    Return the log posterior for given theta 
    Parameters:
    -----------
    theta:   numpy array
             vector location in parameter space
    data:    numpy array
    covmat:  numpy array
             covariance matrix for data points
    """
    # TODO implement log posterior
    # Hint: you can test for infinity values in x with np.isfinite(x) to avoid calculations with infinity 
    ...
    
    return result


### Exercise 2: Gaussian proposal step and the actual sampler

Sampler is supposed to be coded to run for a fixed number of steps specified by the user.

In [ ]:
def gaussian_proposal(theta, U, eigv, step_k):
    """
    Propose step in parameter space starting from given location
    Parameters:
    -----------
    theta:          numpy array
                    vector (length D) with current location in parameter space
    U:              numpy array 
                    DxD tensor of eigenvectors of the inverse of proposal density covariance
    eigv:           numpy array
                    (length D) eigenvalues of the inverse of proposal density covariance
    step_k:         integer
                    step number in the chain (used in sequential updating of parameters)
    Returns:
    --------
    new_theta:  numpy array, new location in parameter space
    """
    
    # Initialize random seed
    rd.seed()
    
    # get the jumps in each parameter
    sigmas = np.zeros(len(theta))
    
    for i in range(len(theta)):
    
        # TODO: sample from (multivariate) Gaussian proposal density
        ...
        
    # TODO calc new position in parameter space
    new_theta = ...
    
    return new_theta

def metropolis_sampler(start_location, psi, data, covmat, K):
    """
    Run a Markov chain of fixed length using the Metropolis/Metropolis-Hastings MCMC algorithm
    Parameters:
    -----------
    start_location: numpy array
                    parameter vector (length D) specifying starting point for the chain
    psi:            numpy array
                    DxD covariance matrix for proposal density
    data:           numpy array
                    data vector (length N) for use in likelihood function
    covmat:         numpy array
                    NxN covariance matrix for data, for use in likelihood
    K:              integer
                    number of steps to run chain for
    
    """
    
    # initialize chain
    chain = np.zeros((K, len(start_location) + 2))
    
    # set 0th column of chain to 1, as we will repeat samples in the chain but this ensures compatibility with GetDist
    chain[:, 0] = 1
    chain[0, 2:] = start_location
    
    # find starting posterior value     
    logprob = lnprob(start_location, data, covmat) 
    max_logprob = logprob
    
    # chain column 1 stores minus log posterior
    chain[0, 1] = -logprob
    
    # find eigenvalues and eigenvectors of the proposal covariance
    sigma_eigv, U = np.linalg.eig(np.linalg.inv(psi))
    
    # keep track of acceptance fraction
    accepted, rejected = 0.0, 0.0
    
    k = 1
    while k < K:
        
        # TODO implement Metropolis algorithm (find proposal, calc (log.)prob, compare to logprob from previous step (needs to be stored until next accepted proposal) & accept or reject and store proposal or old value in chain)
        # Hint: Beware of infinity again ((neg.)infinite logprob => prob =0 => automatic rejection)
        # Hint2: You can find the current state at the end of the chain (i.e. chain[k-1:0])
        new_posn = ...
        new_logprob = ... 
        
        ...
        
        if k % 5000 == 0:
            # output acceptance fraction periodically
            print('Current acceptance fraction, a = %0.2f' %(accepted / (accepted + rejected)))
        
        k += 1
    
    return chain

# Simple tests of MCMC sampling

### Exercise 3: Sample from a 1D Gaussian posterior

Mean 2 and variance 2; run for 5000 steps

In [ ]:
# start from an arbitrary location
start_location = np.array([-1])
# use a proposal width of 1
psi = np.array([[1]])
# specify the posterior to sample from
data = np.array([2])
covmat = np.array([[2]])

chain = metropolis_sampler(start_location, psi, data, covmat, 5001)
# set no. of steps to 5001 just to get the acceptance rate print statement!

# plot a normalised histogram of samples and compare to the true posterior
plt.figure(figsize=(8,6))
_ = plt.hist(chain[:, 2], density=True, histtype='step', bins=100, lw=2, label='sampling')
x = np.linspace(np.min(chain[:, 2]), np.max(chain[:, 2]))
plt.plot(x, np.exp(-(x-2)**2 / 4) / (2*np.sqrt(np.pi)), label='true posterior')
plt.tick_params(labelsize=16)
plt.xlabel('$x$', fontsize=20)
plt.ylabel('$p(x)$', fontsize=20)


View a trace plot of the parameter values in the chain

In [ ]:
plt.plot(chain[:, 2])
plt.xlabel('Number of steps', fontsize=20)
plt.ylabel('$x$', fontsize=20)
plt.tick_params(labelsize=16)

In [ ]:
# save this chain for later use in an example
simple_chain = np.copy(chain)

Questions (try to visualize the answer before executing the code):

1. What happens if you set the starting location to a different value, say -10? What change might you see in the trace plot? What change would you need to make to ensure a good sampling?

2. What happens if you change the proposal width to 0.1? To 100? How does this change the appearance of the trace plot? (For the second case you might need to view only the first few hundred steps of the chain to see it clearly.)


### Exercise 4: Sample from a 2D Gaussian posterior

We now have 2 parameters, $x$ and $y$, with a imposed covariance between them. We want to view the 2D distribution as well as the 1D marginalized distributions in $x$ and $y$ – for this we use corner

In [ ]:
# arbitrary start location
start_location = np.array([3, 3])
# assuming no prior knowledge of the posterior, this is a default proposal
psi = np.array([[1.0, 0], [0, 1.0]])

# data vector and covmat specify the posterior to sample from
data = np.array([0, 0])
covmat = np.array([[2.0, 1.2], [1.2, 2.0]])
    
# we will need to run the chain for longer to get good convergence in 2D
chain = metropolis_sampler(start_location, psi, data, covmat, 10001)

fig = corner.corner(chain[:, [2, 3]], 
                    smooth=1, smooth1d=1, bins=30,
                    labels=[r"$x$", r"$y$"],
                    quantiles=[0.16, 0.84],
                    truths=[0, 0],
                    levels=[0.68, 0.95],
                    show_titles=True, title_kwargs={"fontsize": 16}, 
                    label_kwargs={"fontsize": 22})


Here's how to make the same triangle plot but using GetDist. GetDist can do lots of fun stuff, see https://getdist.readthedocs.io/en/latest/plot_gallery.html for a tutorial notebook. It also has an interactive GUI which is good for analysing cosmological MCMC.

In [ ]:
names = ['x', 'y']
labels = ['x', 'y']

samples = MCSamples(samples=chain[:, 2:], names=names, labels=labels, ranges={'x':[-10, 10], 'y':[-10, 10]})

g = plots.getSubplotPlotter(width_inch=6)
g.triangle_plot(samples, filled=True, contour_lws=[1.3])

for i in range(2):
    for ax in g.subplots[i:,i]:
        ax.tick_params(labelsize=18)
        ax.set_ylabel(ax.get_ylabel(), fontsize=24, labelpad=20)
        ax.set_xlabel(ax.get_xlabel(), fontsize=24, labelpad=25)

print(samples.getInlineLatex('x',limit=1))
print(samples.getInlineLatex('y',limit=1))

*[Note that corner and GetDist can sometimes give slightly different estimates of the marginalised uncertainties! I have not investigated this in detail, but it is probably because there are in fact different reasonable choices of how to calculate a 68% C.L. region that need not give the same answer if the posterior is not perfectly Gaussian.]*

Questions:

1. Change the data covariance to make the $x$-$y$ degeneracy much tighter. How does this affect the acceptance rate? Why? What changes might you make to increase the acceptance rate again?


# "Real-world" example: fitting a straight line to noisy data

This example is taken from the emcee demonstration (http://dfm.io/emcee/current/user/line/), but we want to compare different approaches (M-H vs. emcee vs. non-MCMC methods). For a good discussion of fitting a straight line to data, you should read Hogg et al., https://arxiv.org/abs/1008.4686

### Generate some noisy data

The generative model is a straight line but errors in $y$ are underestimated by a constant fractional amount

In [ ]:
# Choose the "true" parameters.
m_true = -0.9594
b_true = 4.294
f_true = 0.534

# Generate some synthetic data from the model.
N = 50
x = np.sort(10*np.random.rand(N))
y = m_true * x + b_true

# "known" error
yerr = 0.1 + 0.7*np.random.rand(N)
y += yerr * np.random.randn(N)
# "unknown" error
y += np.abs(f_true * y) * np.random.randn(N)

print('True parameters: b = %0.3f, m = %0.3f, f = %0.3f (ln f = %0.3f)' %(b_true, m_true, f_true, np.log(f_true)))

plt.figure(figsize=(8, 6))
plt.errorbar(x, y, yerr=yerr, c='k', fmt='.', markersize=8, elinewidth=1.5, capsize=3, capthick=1.5, label='data')
plt.plot(x, m_true * x + b_true, label='true model')
plt.tick_params(labelsize=16)
plt.xlabel('$x$', fontsize=20)
plt.ylabel('$y$', fontsize=20)
plt.legend(loc='upper right', numpoints=1, frameon=False, fontsize=14)

### Exercise 5: Naive least-squares fit to this data

Let's do a naive least-squares fit first. This *cannot* account for the unknown underestimate of the errors in $y$. It produces some values of $m$ and $b$ but of course no idea of uncertainty in these values. (Note that the actual model fit can sometimes still be quite close to the truth.) 

In [2]:
# TODO least square fit for b_ls and m_ls
...
b_ls, m_ls = ...

print('Least squares fit: b = %0.3f, m = %0.3f' %(b_ls, m_ls))

plt.figure(figsize=(8, 6))
plt.errorbar(x, y, yerr=yerr, c='k', fmt='.', markersize=8, elinewidth=1.5, capsize=3, capthick=1.5, label='data')
plt.plot(x, m_true * x + b_true, label='true model')
plt.plot(x, m_ls * x + b_ls, ls='--', label='least squares estimate')
plt.tick_params(labelsize=16)
plt.xlabel('$x$', fontsize=20)
plt.ylabel('$y$', fontsize=20)
plt.legend(loc='upper right', numpoints=1, frameon=False, fontsize=14)

SyntaxError: invalid syntax (<ipython-input-2-c3c4d7f60216>, line 3)

### Exercise 6: A better maximum-likelihood estimation

Define a log-likelihood function, prior and posterior for this specific problem. Note here we use $ln(f)$ instead of $f$ to help with the later sampling. 

In [3]:
def lnlike(theta, data, covmat):
    m, b, lnf = theta
    x = data[0]
    y = data[1]
    yerr = np.sqrt(np.diag(covmat))
    
    # TODO define model (linear) and calculate inverse cov. for this model to calculate likelihood
    model = ...
    ...
    
    return result

def lnprior(theta):
    m, b, lnf = theta
    
    #TODO define log flat prior with m in ]-5.0,0.5[, b in ]0,10[ and lnf in ]-10,1[
    ...
    
    return result

def lnprob(theta, data, covmat):
    
    x = data[0]
    y = data[1]        
    yerr = np.sqrt(np.diag(covmat))
    
    #TODO calc log posterior
    ...
    return result

SyntaxError: invalid syntax (<ipython-input-3-80f4d68a4444>, line 8)

Optimise to find maximum likelihood (ML) estimate. This is better than naive least squares (obviously), but still doesn't give uncertainties.

In [4]:
import scipy.optimize as op
nll = lambda *args: -lnlike(*args)

data = np.vstack([x, y])
covmat = np.diag(yerr * yerr)

result = op.minimize(nll, [m_true, b_true, np.log(f_true)], args=(data, covmat))
m_ml, b_ml, lnf_ml = result["x"]

print('Maximum likelihood optimization: b = %0.3f, m = %0.3f, f = %0.3f (ln f = %0.3f)' 
      %(b_ml, m_ml, np.exp(lnf_ml), lnf_ml))

plt.figure(figsize=(8, 6))
plt.errorbar(x, y, yerr=yerr, c='k', fmt='.', markersize=8, elinewidth=1.5, capsize=3, capthick=1.5, label='data')
plt.plot(x, m_true * x + b_true, label='true model')
plt.plot(x, m_ls * x + b_ls, ls='--', label='least squares estimate')
plt.plot(x, m_ml * x + b_ml, ls='--', label='max. likelihood estimate')
plt.tick_params(labelsize=16)
plt.xlabel('$x$', fontsize=20)
plt.ylabel('$y$', fontsize=20)
plt.legend(loc='upper right', numpoints=1, frameon=False, fontsize=14)

NameError: name 'x' is not defined

### Exercise 7: Sampling with M-H MCMC (initial)

Try sampling from the posterior using Metropolis-Hastings. Choose the start location at the maximum-likelihood point. We don't know a good proposal matrix yet, so let's start with a diagonal matrix with "guesstimated" step size.

In [ ]:
start_location = np.array([m_ml, b_ml, lnf_ml])
psi = np.array([[0.2, 0, 0], [0, 0.2, 0], [0, 0, 0.2]])

start = time.time()
chain = metropolis_sampler(start_location, psi, data, covmat, 10001)
stop = time.time()
print('Time elapsed: %0.2f' %(stop-start))

Acceptance fraction is very low! Why? What should we conclude?

Check trace plots – these confirm that the chain is not well converged even after 10000 steps.

In [ ]:
fig, axes = plt.subplots(3, 1, figsize=(8,6), sharex=True)

ax = axes.flat[0]
ax.plot(chain[:, 2])
ax.tick_params(labelsize=16)
ax.set_ylabel('$m$', fontsize=20)
ax = axes.flat[1]
ax.plot(chain[:, 3])
ax.tick_params(labelsize=16)
ax.set_ylabel('$b$', fontsize=20)
ax = axes.flat[2]
ax.plot(chain[:, 4])
ax.tick_params(labelsize=16)
ax.set_ylabel('$\ln(f)$', fontsize=20)
ax.set_xlabel('Number of steps', fontsize=20)


If we make corner plots, the lack of convergence is obvious here too. Can you also see the reason why we did not converge?

In [ ]:
fig = corner.corner(chain[:, 2:], 
                    smooth=1, smooth1d=1, bins=30,
                    labels=[r"$m$", r"$b$", r"$\ln(f)$"],
                    truths=[m_true, b_true, np.log(f_true)],
                    levels=[0.68, 0.95],
                    show_titles=True, title_kwargs={"fontsize": 16}, 
                    label_kwargs={"fontsize": 22})


### Exercise 8: Sampling with M-H MCMC (final)

The previous run did not converge because we used a poor proposal. Let's tune the proposal using this information and try again.

In [ ]:
# estimate the covariance of the the parameters from the initial chain, use this as the proposal
diffs = chain[:, 2:] - np.mean(chain[:, 2:], axis=0)
psi = np.cov(diffs, rowvar=False)

start = time.time()
chain = metropolis_sampler(start_location, psi, data, covmat, 10001)
stop = time.time()
print('Time elapsed: %0.2f' %(stop-start))

The acceptance fraction is now much better. This heuristic suggests the chain is probably better converged.

Look at the trace plots: the chain traverses the allowed range of parameter space several times, again suggesting convergence. 
**Note**: For more serious convergence testing, bear in mind:

1. We can (almost) *never* guarantee we have correctly sampled the posterior
2. The error in the sampling is small when the chain length is much longer than the integrated autocorrelation time $\tau_\mathrm{int}$. Estimating $\tau_\mathrm{int}$ is hard, I won't cover it here. But you can estimate the ratio $\tau_\mathrm{int}/N$ "by eye" from the trace plots.
3. A further necessary test of good sampling is to run several chains with different starting positions and check they end up sampling the same posterior mode. I haven't bothered with this here.

In [ ]:
fig, axes = plt.subplots(3, 1, figsize=(8,6), sharex=True)

ax = axes.flat[0]
ax.plot(chain[:, 2])
ax.tick_params(labelsize=16)
ax.set_ylabel('$m$', fontsize=20)
ax = axes.flat[1]
ax.plot(chain[:, 3])
ax.tick_params(labelsize=16)
ax.set_ylabel('$b$', fontsize=20)
ax = axes.flat[2]
ax.plot(chain[:, 4])
ax.tick_params(labelsize=16)
ax.set_ylabel('$\ln(f)$', fontsize=20)
ax.set_xlabel('Number of steps', fontsize=20)


Now look at the corner plots:

In [ ]:
fig = corner.corner(chain[:, 2:], 
                    smooth=1, smooth1d=1, bins=30,
                    labels=[r"$m$", r"$b$", r"$\ln(f)$"],
                    truths=[m_true, b_true, np.log(f_true)],
                    levels=[0.68, 0.95],
                    show_titles=False, title_kwargs={"fontsize": 16}, 
                    label_kwargs={"fontsize": 22})


Quote final results from MCMC analysis (this is one of the reasonable options for doing this):

In [ ]:
param_values = chain[:, 2:]
param_values[:, 2] = np.exp(param_values[:, 2])
m_mcmc, b_mcmc, f_mcmc = map(lambda v: (v[1], v[2]-v[1], v[1]-v[0]),
                             zip(*np.percentile(param_values, [16, 50, 84],
                                                axis=0)))
print('Marginalized median results:\n')
print('\tm = %0.2f^{+%0.2f}_{-%0.2f}\n' % m_mcmc)
print('\tb = %0.2f^{+%0.2f}_{-%0.2f}\n' % b_mcmc)
print('\tf = %0.2f^{+%0.2f}_{-%0.2f}\n' % f_mcmc)
print('Compare to truth: m = %0.3f, b = %0.3f, f = %0.3f' % (m_true, b_true, f_true))

Another good way to visualize the results: posterior predictive plots for models selected randomly from the sampled posterior

In [ ]:
plt.figure(figsize=(8, 6))
first_label = True
for m, b, lnf in chain[np.random.randint(len(chain), size=100), 2:]:
    if first_label:
        plt.plot(x, m*x + b, color="grey", lw=0.7, alpha=0.2, label='posterior samples')
        first_label = False
    else:
        plt.plot(x, m*x + b, color="grey", lw=0.7, alpha=0.2)

plt.plot(x, m_true * x + b_true, lw=2, c='tomato', label='true model')
plt.errorbar(x, y, yerr=yerr, c='k', fmt='.', markersize=8, elinewidth=1.5, capsize=3, capthick=1.5, label='data')
plt.tick_params(labelsize=16)
plt.xlabel('$x$', fontsize=20)
plt.ylabel('$y$', fontsize=20)
plt.legend(loc='upper right', numpoints=1, frameon=False, fontsize=14)


### Exercise 9: Sample the same posterior using **emcee**

**emcee** is a Python implementation of an affine-invariant ensemble sampler method. See Foreman-Mackey et al., https://arxiv.org/abs/1202.3665 for the code paper, Goodman & Weare, 2010, Comm. App. Math. Comp. Sci., 5, 65 for the algorithm, http://dfm.io/emcee/current/ for download and usage instructions. 

In [ ]:
ndim, nwalkers = 3, 100
# for emcee it is best to start all walkers in a tight ball near the ML point
pos = [result["x"] + 1e-4*np.random.randn(ndim) for i in range(nwalkers)]

sampler = emcee.EnsembleSampler(nwalkers, ndim, lnprob, args=(data, covmat))
start = time.time()
sampler.run_mcmc(pos, 2000);
stop = time.time()
print('Time to run = %0.2f seconds' %(stop-start))

**Notes**:

1. **emcee** does not require an input proposal matrix. We simply used 100 walkers, and each walker ran for 2000 steps.

2. Overall, this **emcee** run takes almost the same time as the final (tuned) M-H sampling; but it didn't require the intial tuning step. (But also note that this is very simple M-H sampler, which could almost certainly be optimized for speed.)

3. In the end, **emcee** has given us 200,000 samples (vs. 10,000 from final M-H run). These samples are ***not*** from independent chains though!

Check trace plots for a sub-sample of walkers. Taken together the walkers sample the parameter space well, but note that each walker (different colour chains) has a very long autocorrelation time!

In [ ]:
fig, axes = plt.subplots(3, 1, figsize=(8,6), sharex=True)

ax = axes.flat[0]
for i in range(20):
    ax.plot(sampler.chain[i, :, 0])  # note how to access parameter positions in the chain!
ax.tick_params(labelsize=16)
ax.set_ylabel('$m$', fontsize=20)
ax = axes.flat[1]
for i in range(20):
    ax.plot(sampler.chain[i, :, 1])  
ax.tick_params(labelsize=16)
ax.set_ylabel('$b$', fontsize=20)
ax = axes.flat[2]
for i in range(20):
    ax.plot(sampler.chain[i, :, 2])  
ax.tick_params(labelsize=16)
ax.set_ylabel('$\ln(f)$', fontsize=20)
ax.set_xlabel('Number of steps', fontsize=20)



Zoom in on the beginning of the trace plots: notice how the walkers very quickly (within ~50 steps) expand out from the tight initial starting ball to sample the full parameter space. Based on this, a conservative choice of burn-in to discard is maybe 100 steps.

In [ ]:
fig, axes = plt.subplots(3, 1, figsize=(8,6), sharex=True)

ax = axes.flat[0]
for i in range(20):
    ax.plot(sampler.chain[i, :200, 0])  # note how to access parameter positions in the chain!
ax.tick_params(labelsize=16)
ax.set_ylabel('$m$', fontsize=20)
ax = axes.flat[1]
for i in range(20):
    ax.plot(sampler.chain[i, :200, 1])  
ax.tick_params(labelsize=16)
ax.set_ylabel('$b$', fontsize=20)
ax = axes.flat[2]
for i in range(20):
    ax.plot(sampler.chain[i, :200, 2])  
ax.tick_params(labelsize=16)
ax.set_ylabel('$\ln(f)$', fontsize=20)
ax.set_xlabel('Number of steps', fontsize=20)



Corner plots from the **emcee** sampling

In [ ]:
# discard 100 steps of burn-in and join samples from all walkers together
samples = sampler.chain[:, 100:, :].reshape((-1, ndim))

fig = corner.corner(samples[:, :], 
                    smooth=1, smooth1d=1, bins=30,
                    labels=[r"$m$", r"$b$", r"$\ln(f)$"],
                    truths=[m_true, b_true, np.log(f_true)],
                    levels=[0.68, 0.95],
                    show_titles=True, title_kwargs={"fontsize": 16}, 
                    label_kwargs={"fontsize": 22})


**emcee** headline results and posterior predictive plots: compare these with those from the M-H sampling above

In [ ]:
plt.figure(figsize=(8, 6))
first_label = True
for m, b, lnf in samples[np.random.randint(len(samples), size=100)]:
    if first_label:
        plt.plot(x, m*x + b, color="grey", lw=0.7, alpha=0.3, label='posterior samples')
        first_label = False
    else:
        plt.plot(x, m*x + b, color="grey", lw=0.7, alpha=0.2)

plt.plot(x, m_true * x + b_true, lw=2, c='tomato', label='true model')
plt.errorbar(x, y, yerr=yerr, c='k', fmt='.', markersize=8, elinewidth=1.5, capsize=3, capthick=1.5, label='data')
plt.tick_params(labelsize=16)
plt.xlabel('$x$', fontsize=20)
plt.ylabel('$y$', fontsize=20)
plt.legend(loc='upper right', numpoints=1, frameon=False, fontsize=14)

samples = sampler.chain[:, 50:, :].reshape((-1, ndim))
samples[:, 2] = np.exp(samples[:, 2])
m_mcmc, b_mcmc, f_mcmc = map(lambda v: (v[1], v[2]-v[1], v[1]-v[0]),
                             zip(*np.percentile(samples, [16, 50, 84],
                                                axis=0)))
print('Marginalized median results:\n')
print('\tm = %0.2f^{+%0.2f}_{-%0.2f}\n' % m_mcmc )
print('\tb = %0.2f^{+%0.2f}_{-%0.2f}\n' % b_mcmc)
print('\tf = %0.2f^{+%0.2f}_{-%0.2f}\n' % f_mcmc)
print('Compare to truth: m = %0.3f, b = %0.3f, f = %0.3f' % (m_true, b_true, f_true))

# Special Thanks

To Dr Sethadri Nadathur for allowing me to use part of his excellent course material for this tutorial

# Reading / further material

In addition to the papers and websites highlighted above, you can also have a look at:

1. https://m-clark.github.io/docs/ld_mcmc/: A list of MCMC algorithms, with a short description and summary of each, plus references to the literature

2. https://gabriel-p.github.io/pythonMCMC/: A list of public Python-based MCMC packages. One of these might be useful if you need something more powerful than your home-made M-H sampler!

3. CosmoHammer, Akeret et al, https://arxiv.org/abs/1212.1721: an implementation of emcee for cosmological analysis (i.e. fitting CMB data), that scales to use thousands of cores